# Project 3: Smart Beta Portfolio and Portfolio Optimization

## Overview


Smart beta has a broad meaning, but we can say in practice that when we use the universe of stocks from an index, and then apply some weighting scheme other than market cap weighting, it can be considered a type of smart beta fund.  A Smart Beta portfolio generally gives investors exposure or "beta" to one or more types of market characteristics (or factors) that are believed to predict prices while giving investors a diversified broad exposure to a particular market. Smart Beta portfolios generally target momentum, earnings quality, low volatility, and dividends or some combination. Smart Beta Portfolios are generally rebalanced infrequently and follow relatively simple rules or algorithms that are passively managed.  Model changes to these types of funds are also rare requiring prospectus filings with US Security and Exchange Commission in the case of US focused mutual funds or ETFs.. Smart Beta portfolios are generally long-only, they do not short stocks.

In contrast, a purely alpha-focused quantitative fund may use multiple models or algorithms to create a portfolio. The portfolio manager retains discretion in upgrading or changing the types of models and how often to rebalance the portfolio in attempt to maximize performance in comparison to a stock benchmark.  Managers may have discretion to short stocks in portfolios.

Imagine you're a portfolio manager, and wish to try out some different portfolio weighting methods.

One way to design portfolio is to look at certain accounting measures (fundamentals) that, based on past trends, indicate stocks that produce better results.  


For instance, you may start with a hypothesis that dividend-issuing stocks tend to perform better than stocks that do not. This may not always be true of all companies; for instance, Apple does not issue dividends, but has had good historical performance.  The hypothesis about dividend-paying stocks may go something like this: 

Companies that regularly issue dividends may also be more prudent in allocating their available cash, and may indicate that they are more conscious of prioritizing shareholder interests.  For example, a CEO may decide to reinvest cash into pet projects that produce low returns.  Or, the CEO may do some analysis, identify that reinvesting within the company produces lower returns compared to a diversified portfolio, and so decide that shareholders would be better served if they were given the cash (in the form of dividends).  So according to this hypothesis, dividends may be both a proxy for how the company is doing (in terms of earnings and cash flow), but also a signal that the company acts in the best interest of its shareholders.  Of course, it's important to test whether this works in practice.


You may also have another hypothesis, with which you wish to design a portfolio that can then be made into an ETF.  You may find that investors may wish to invest in passive beta funds, but wish to have less risk exposure (less volatility) in their investments.  The goal of having a low volatility fund that still produces returns similar to an index may be appealing to investors who have a shorter investment time horizon, and so are more risk averse.

So the objective of your proposed portfolio is to design a portfolio that closely tracks an index, while also minimizing the portfolio variance.  Also, if this portfolio can match the returns of the index with less volatility, then it has a higher risk-adjusted return (same return, lower volatility).

Smart Beta ETFs can be designed with both of these two general methods (among others): alternative weighting and minimum volatility ETF.


## Instructions
Each problem consists of a function to implement and instructions on how to implement the function.  The parts of the function that need to be implemented are marked with a `# TODO` comment. After implementing the function, run the cell to test it against the unit tests we've provided. For each problem, we provide one or more unit tests from our `project_tests` package. These unit tests won't tell you if your answer is correct, but will warn you of any major errors. Your code will be checked for the correct solution when you submit it to Udacity.

## Packages
When you implement the functions, you'll only need to you use the packages you've used in the classroom, like [Pandas](https://pandas.pydata.org/) and [Numpy](http://www.numpy.org/). These packages will be imported for you. We recommend you don't add any import statements, otherwise the grader might not be able to run your code.

The other packages that we're importing are `helper`, `project_helper`, and `project_tests`. These are custom packages built to help you solve the problems.  The `helper` and `project_helper` module contains utility functions and graph functions. The `project_tests` contains the unit tests for all the problems.
### Install Packages

In [2]:
import sys
!{sys.executable} -m pip install -r requirements.txt

  Using cached numpy-1.14.5-cp36-cp36m-manylinux1_x86_64.whl (12.2 MB)
  Attempting uninstall: numpy
    Found existing installation: numpy 1.19.5
    Uninstalling numpy-1.19.5:
      Successfully uninstalled numpy-1.19.5
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
tensorflow 2.6.2 requires numpy~=1.19.2, but you have numpy 1.14.5 which is incompatible.
tensorflow 2.6.2 requires six~=1.15.0, but you have six 1.11.0 which is incompatible.
tensorboard 2.6.0 requires requests<3,>=2.21.0, but you have requests 2.18.4 which is incompatible.
moviepy 0.2.3.2 requires tqdm==4.11.2, but you have tqdm 4.19.5 which is incompatible.


In [3]:
!python -m pip install plotly==3.10.0 --no-cache

In [4]:
# Restart the Kernel
import plotly
print(plotly.__version__)
# Should return plotly==3.10.0

3.10.0


### Load Packages

In [5]:
import pandas as pd
import numpy as np
import helper
import project_helper
import project_tests

## Market Data
### Load Data
For this universe of stocks, we'll be selecting large dollar volume stocks. We're using this universe, since it is highly liquid.

In [27]:
df = pd.read_csv('../../data/project_3/eod-quotemedia.csv')

percent_top_dollar = 0.2
high_volume_symbols = project_helper.large_dollar_volume_stocks(df, 'adj_close', 'adj_volume', percent_top_dollar)
df = df[df['ticker'].isin(high_volume_symbols)]

close = df.reset_index().pivot(index='date', columns='ticker', values='adj_close')
volume = df.reset_index().pivot(index='date', columns='ticker', values='adj_volume')
dividends = df.reset_index().pivot(index='date', columns='ticker', values='dividends')

### View Data
To see what one of these 2-d matrices looks like, let's take a look at the closing prices matrix.

In [7]:
project_helper.print_dataframe(close)

# Part 1: Smart Beta Portfolio
In Part 1 of this project, you'll build a portfolio using dividend yield to choose the portfolio weights. A portfolio such as this could be incorporated into a smart beta ETF.  You'll compare this portfolio to a market cap weighted index to see how well it performs. 

Note that in practice, you'll probably get the index weights from a data vendor (such as companies that create indices, like MSCI, FTSE, Standard and Poor's), but for this exercise we will simulate a market cap weighted index.

## Index Weights
The index we'll be using is based on large dollar volume stocks. Implement `generate_dollar_volume_weights` to generate the weights for this index. For each date, generate the weights based on dollar volume traded for that date. For example, assume the following is close prices and volume data:
```
                 Prices
               A         B         ...
2013-07-08     2         2         ...
2013-07-09     5         6         ...
2013-07-10     1         2         ...
2013-07-11     6         5         ...
...            ...       ...       ...

                 Volume
               A         B         ...
2013-07-08     100       340       ...
2013-07-09     240       220       ...
2013-07-10     120       500       ...
2013-07-11     10        100       ...
...            ...       ...       ...
```
The weights created from the function `generate_dollar_volume_weights` should be the following:
```
               A         B         ...
2013-07-08     0.126..   0.194..   ...
2013-07-09     0.759..   0.377..   ...
2013-07-10     0.075..   0.285..   ...
2013-07-11     0.037..   0.142..   ...
...            ...       ...       ...
```

In [8]:
def generate_dollar_volume_weights(close, volume):
    """
    Generate dollar volume weights.

    Parameters
    ----------
    close : DataFrame
        Close price for each ticker and date
    volume : str
        Volume for each ticker and date

    Returns
    -------
    dollar_volume_weights : DataFrame
        The dollar volume weights for each ticker and date
    """
    assert close.index.equals(volume.index)
    assert close.columns.equals(volume.columns)
    
    #TODO: Implement function
    
    result = pd.DataFrame(columns=close.columns)
    for index, (close_row, volume_row) in enumerate(zip(close.iterrows(), volume.iterrows())):
        _, close_values = close_row
        _, volume_values = volume_row
    
        # Element-wise multiplication
        row_result = close_values * volume_values
    
        # Sum the multiplication results and append as a new row to the result dataframe
        result = result.append(pd.Series(row_result.sum(), index=result.columns), ignore_index=True)
        
    weights = close.copy()

    # Iterate over each row of the dataframes
    for index, (close_row, volume_row) in enumerate(zip(close.iterrows(), volume.iterrows())):
        _, close_values = close_row
        _, volume_values = volume_row
    
        # Element-wise multiplication
        multiplication_result = close_values * volume_values
    
        # Element-wise division by the corresponding values in the result dataframe
        row_weights = multiplication_result / result.iloc[index]
    
        # Update the corresponding row in the weights dataframe with the calculated values
        weights.iloc[index] = row_weights

    return weights

project_tests.test_generate_dollar_volume_weights(generate_dollar_volume_weights)

Tests Passed


### View Data
Let's generate the index weights using `generate_dollar_volume_weights` and view them using a heatmap.

In [9]:
index_weights = generate_dollar_volume_weights(close, volume)
project_helper.plot_weights(index_weights, 'Index Weights')

## Portfolio Weights
Now that we have the index weights, let's choose the portfolio weights based on dividend. You would normally calculate the weights based on trailing dividend yield, but we'll simplify this by just calculating the total dividend yield over time.

Implement `calculate_dividend_weights` to return the weights for each stock based on its total dividend yield over time. This is similar to generating the weight for the index, but it's using dividend data instead.
For example, assume the following is `dividends` data:
```
                 Prices
               A         B
2013-07-08     0         0
2013-07-09     0         1
2013-07-10     0.5       0
2013-07-11     0         0
2013-07-12     2         0
...            ...       ...
```
The weights created from the function `calculate_dividend_weights` should be the following:
```
               A         B
2013-07-08     NaN       NaN
2013-07-09     0         1
2013-07-10     0.333..   0.666..
2013-07-11     0.333..   0.666..
2013-07-12     0.714..   0.285..
...            ...       ...
```

In [10]:
def calculate_dividend_weights(dividends):
    """
    Calculate dividend weights.

    Parameters
    ----------
    dividends : DataFrame
        Dividend for each stock and date

    Returns
    -------
    dividend_weights : DataFrame
        Weights for each stock and date
    """
    #TODO: Implement function
    dividends_copy = dividends.copy()
    dividends_copy = np.cumsum(dividends_copy)
    total = dividends_copy.sum(axis=1)
    dividend_weights = dividends_copy.divide(total, axis='rows')

    return dividend_weights

project_tests.test_calculate_dividend_weights(calculate_dividend_weights)

Tests Passed


### View Data
Just like the index weights, let's generate the ETF weights and view them using a heatmap.

In [11]:
etf_weights = calculate_dividend_weights(dividends)
project_helper.plot_weights(etf_weights, 'ETF Weights')

## Returns
Implement `generate_returns` to generate returns data for all the stocks and dates from price data. You might notice we're implementing returns and not log returns. Since we're not dealing with volatility, we don't have to use log returns.

In [12]:
def generate_returns(prices):
    """
    Generate returns for ticker and date.

    Parameters
    ----------
    prices : DataFrame
        Price for each ticker and date

    Returns
    -------
    returns : Dataframe
        The returns for each ticker and date
    """
    #TODO: Implement function
    prices_t = prices.shift(1)
    returns = (prices - prices_t) / prices_t

    return returns

project_tests.test_generate_returns(generate_returns)

Tests Passed


### View Data
Let's generate the closing returns using `generate_returns` and view them using a heatmap.

In [13]:
returns = generate_returns(close)
project_helper.plot_returns(returns, 'Close Returns')

## Weighted Returns
With the returns of each stock computed, we can use it to compute the returns for an index or ETF. Implement `generate_weighted_returns` to create weighted returns using the returns and weights.

In [14]:
def generate_weighted_returns(returns, weights):
    """
    Generate weighted returns.

    Parameters
    ----------
    returns : DataFrame
        Returns for each ticker and date
    weights : DataFrame
        Weights for each ticker and date

    Returns
    -------
    weighted_returns : DataFrame
        Weighted returns for each ticker and date
    """
    assert returns.index.equals(weights.index)
    assert returns.columns.equals(weights.columns)
    
    #TODO: Implement function
    

    return returns * weights

project_tests.test_generate_weighted_returns(generate_weighted_returns)

Tests Passed


### View Data
Let's generate the ETF and index returns using `generate_weighted_returns` and view them using a heatmap.

In [15]:
index_weighted_returns = generate_weighted_returns(returns, index_weights)
etf_weighted_returns = generate_weighted_returns(returns, etf_weights)
project_helper.plot_returns(index_weighted_returns, 'Index Returns')
project_helper.plot_returns(etf_weighted_returns, 'ETF Returns')

## Cumulative Returns
To compare performance between the ETF and Index, we're going to calculate the tracking error. Before we do that, we first need to calculate the index and ETF comulative returns. Implement `calculate_cumulative_returns` to calculate the cumulative returns over time given the returns.

In [16]:
def calculate_cumulative_returns(returns):
    """
    Calculate cumulative returns.

    Parameters
    ----------
    returns : DataFrame
        Returns for each ticker and date

    Returns
    -------
    cumulative_returns : Pandas Series
        Cumulative returns for each date
    """
    #TODO: Implement function
    cum_return = returns.sum(axis=1)
    cum_return = cum_return + 1
    cum_return = np.cumprod(cum_return, axis=0)
    cum_return.iloc[0] = np.nan
    
    return cum_return

project_tests.test_calculate_cumulative_returns(calculate_cumulative_returns)

Tests Passed


### View Data
Let's generate the ETF and index cumulative returns using `calculate_cumulative_returns` and compare the two.

In [17]:
index_weighted_cumulative_returns = calculate_cumulative_returns(index_weighted_returns)
etf_weighted_cumulative_returns = calculate_cumulative_returns(etf_weighted_returns)
project_helper.plot_benchmark_returns(index_weighted_cumulative_returns, etf_weighted_cumulative_returns, 'Smart Beta ETF vs Index')

## Tracking Error
In order to check the performance of the smart beta portfolio, we can calculate the annualized tracking error against the index. Implement `tracking_error` to return the tracking error between the ETF and benchmark.

For reference, we'll be using the following annualized tracking error function:
$$ TE = \sqrt{252} * SampleStdev(r_p - r_b) $$

Where $ r_p $ is the portfolio/ETF returns and $ r_b $ is the benchmark returns.

_Note: When calculating the sample standard deviation, the delta degrees of freedom is 1, which is the also the default value._

In [18]:
def tracking_error(benchmark_returns_by_date, etf_returns_by_date):
    """
    Calculate the tracking error.

    Parameters
    ----------
    benchmark_returns_by_date : Pandas Series
        The benchmark returns for each date
    etf_returns_by_date : Pandas Series
        The ETF returns for each date

    Returns
    -------
    tracking_error : float
        The tracking error
    """
    assert benchmark_returns_by_date.index.equals(etf_returns_by_date.index)
    
    #TODO: Implement function
    
    returns_diff = etf_returns_by_date - benchmark_returns_by_date
    sum_returns_diff_sq = np.std(returns_diff,ddof=1)
    tracking_error = np.sqrt(252) * sum_returns_diff_sq
    
    return tracking_error

project_tests.test_tracking_error(tracking_error)

Tests Passed


### View Data
Let's generate the tracking error using `tracking_error`.

In [19]:
smart_beta_tracking_error = tracking_error(np.sum(index_weighted_returns, 1), np.sum(etf_weighted_returns, 1))
print('Smart Beta Tracking Error: {}'.format(smart_beta_tracking_error))

Smart Beta Tracking Error: 0.1020761483200753


# Part 2: Portfolio Optimization

Now, let's create a second portfolio.  We'll still reuse the market cap weighted index, but this will be independent of the dividend-weighted portfolio that we created in part 1.

We want to both minimize the portfolio variance and also want to closely track a market cap weighted index.  In other words, we're trying to minimize the distance between the weights of our portfolio and the weights of the index.

$Minimize \left [ \sigma^2_p + \lambda \sqrt{\sum_{1}^{m}(weight_i - indexWeight_i)^2} \right  ]$ where $m$ is the number of stocks in the portfolio, and $\lambda$ is a scaling factor that you can choose.

Why are we doing this? One way that investors evaluate a fund is by how well it tracks its index. The fund is still expected to deviate from the index within a certain range in order to improve fund performance.  A way for a fund to track the performance of its benchmark is by keeping its asset weights similar to the weights of the index.  We’d expect that if the fund has the same stocks as the benchmark, and also the same weights for each stock as the benchmark, the fund would yield about the same returns as the benchmark. By minimizing a linear combination of both the portfolio risk and distance between portfolio and benchmark weights, we attempt to balance the desire to minimize portfolio variance with the goal of tracking the index.


## Covariance
Implement `get_covariance_returns` to calculate the covariance of the `returns`. We'll use this to calculate the portfolio variance.

If we have $m$ stock series, the covariance matrix is an $m \times m$ matrix containing the covariance between each pair of stocks.  We can use [`Numpy.cov`](https://docs.scipy.org/doc/numpy/reference/generated/numpy.cov.html) to get the covariance.  We give it a 2D array in which each row is a stock series, and each column is an observation at the same period of time. For any `NaN` values, you can replace them with zeros using the [`DataFrame.fillna`](https://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.fillna.html) function.

The covariance matrix $\mathbf{P} = 
\begin{bmatrix}
\sigma^2_{1,1} & ... & \sigma^2_{1,m} \\ 
... & ... & ...\\
\sigma_{m,1} & ... & \sigma^2_{m,m}  \\
\end{bmatrix}$

In [20]:
def get_covariance_returns(returns):
    """
    Calculate covariance matrices.

    Parameters
    ----------
    returns : DataFrame
        Returns for each ticker and date

    Returns
    -------
    returns_covariance  : 2 dimensional Ndarray
        The covariance of the returns
    """
    #TODO: Implement function
    
    returns = returns.fillna(0)
    
    return np.cov(returns.transpose())

project_tests.test_get_covariance_returns(get_covariance_returns)

Tests Passed


### View Data
Let's look at the covariance generated from `get_covariance_returns`.

In [28]:
covariance_returns = get_covariance_returns(returns)
covariance_returns = pd.DataFrame(covariance_returns, returns.columns, returns.columns)

covariance_returns_correlation = np.linalg.inv(np.diag(np.sqrt(np.diag(covariance_returns))))
covariance_returns_correlation = pd.DataFrame(
    covariance_returns_correlation.dot(covariance_returns).dot(covariance_returns_correlation),
    covariance_returns.index,
    covariance_returns.columns)

project_helper.plot_covariance_returns_correlation(
    covariance_returns_correlation,
    'Covariance Returns Correlation Matrix')

KeyError: 'xaxis2'

### portfolio variance
We can write the portfolio variance $\sigma^2_p = \mathbf{x^T} \mathbf{P} \mathbf{x}$

Recall that the $\mathbf{x^T} \mathbf{P} \mathbf{x}$ is called the quadratic form.
We can use the cvxpy function `quad_form(x,P)` to get the quadratic form.

### Distance from index weights
We want portfolio weights that track the index closely.  So we want to minimize the distance between them.
Recall from the Pythagorean theorem that you can get the distance between two points in an x,y plane by adding the square of the x and y distances and taking the square root.  Extending this to any number of dimensions is called the L2 norm.  So: $\sqrt{\sum_{1}^{n}(weight_i - indexWeight_i)^2}$  Can also be written as $\left \| \mathbf{x} - \mathbf{index} \right \|_2$.  There's a cvxpy function called [norm()](https://www.cvxpy.org/api_reference/cvxpy.atoms.other_atoms.html#norm)
`norm(x, p=2, axis=None)`.  The default is already set to find an L2 norm, so you would pass in one argument, which is the difference between your portfolio weights and the index weights.

### objective function
We want to minimize both the portfolio variance and the distance of the portfolio weights from the index weights.
We also want to choose a `scale` constant, which is $\lambda$ in the expression. 

$\mathbf{x^T} \mathbf{P} \mathbf{x} + \lambda \left \| \mathbf{x} - \mathbf{index} \right \|_2$


This lets us choose how much priority we give to minimizing the difference from the index, relative to minimizing the variance of the portfolio.  If you choose a higher value for `scale` ($\lambda$).

We can find the objective function using cvxpy `objective = cvx.Minimize()`.  Can you guess what to pass into this function?



### constraints
We can also define our constraints in a list.  For example, you'd want the weights to sum to one. So $\sum_{1}^{n}x = 1$.  You may also need to go long only, which means no shorting, so no negative weights.  So $x_i >0 $ for all $i$. you could save a variable as `[x >= 0, sum(x) == 1]`, where x was created using `cvx.Variable()`.

### optimization
So now that we have our objective function and constraints, we can solve for the values of $\mathbf{x}$.
cvxpy has the constructor `Problem(objective, constraints)`, which returns a `Problem` object.

The `Problem` object has a function solve(), which returns the minimum of the solution.  In this case, this is the minimum variance of the portfolio.

It also updates the vector $\mathbf{x}$.

We can check out the values of $x_A$ and $x_B$ that gave the minimum portfolio variance by using `x.value`

In [23]:
import cvxpy as cvx

def get_optimal_weights(covariance_returns, index_weights, scale=2.0):
    """
    Find the optimal weights.

    Parameters
    ----------
    covariance_returns : 2 dimensional Ndarray
        The covariance of the returns
    index_weights : Pandas Series
        Index weights for all tickers at a period in time
    scale : int
        The penalty factor for weights the deviate from the index 
    Returns
    -------
    x : 1 dimensional Ndarray
        The solution for x
    """
    assert len(covariance_returns.shape) == 2
    assert len(index_weights.shape) == 1
    assert covariance_returns.shape[0] == covariance_returns.shape[1]  == index_weights.shape[0]

    #TODO: Implement function

    m = covariance_returns.shape[0]
    x = cvx.Variable(m)
    portfolio_variance = cvx.quad_form(x, covariance_returns)
    
    distance_to_index = x - index_weights
    
    objective = cvx.Minimize(portfolio_variance + 
                             (scale * cvx.norm(distance_to_index, p=2, axis=None)))

    constraints = [cvx.sum(x) == 1, x >= 0]
    problem = cvx.Problem(objective, constraints)
    min_value = problem.solve()

    x_values = x.value
    
    return x_values

project_tests.test_get_optimal_weights(get_optimal_weights)

Tests Passed


## Optimized Portfolio
Using the `get_optimal_weights` function, let's generate the optimal ETF weights without rebalanceing. We can do this by feeding in the covariance of the entire history of data. We also need to feed in a set of index weights. We'll go with the average weights of the index over time.

In [29]:
raw_optimal_single_rebalance_etf_weights = get_optimal_weights(covariance_returns.values, index_weights.iloc[-1])
optimal_single_rebalance_etf_weights = pd.DataFrame(
    np.tile(raw_optimal_single_rebalance_etf_weights, (len(returns.index), 1)),
    returns.index,
    returns.columns)

With our ETF weights built, let's compare it to the index. Run the next cell to calculate the ETF returns and compare it to the index returns.

In [30]:
optim_etf_returns = generate_weighted_returns(returns, optimal_single_rebalance_etf_weights)
optim_etf_cumulative_returns = calculate_cumulative_returns(optim_etf_returns)
project_helper.plot_benchmark_returns(index_weighted_cumulative_returns, optim_etf_cumulative_returns, 'Optimized ETF vs Index')

optim_etf_tracking_error = tracking_error(np.sum(index_weighted_returns, 1), np.sum(optim_etf_returns, 1))
print('Optimized ETF Tracking Error: {}'.format(optim_etf_tracking_error))

Optimized ETF Tracking Error: 0.05795012630412267


## Rebalance Portfolio Over Time
The single optimized ETF portfolio used the same weights for the entire history. This might not be the optimal weights for the entire period. Let's rebalance the portfolio over the same period instead of using the same weights. Implement `rebalance_portfolio` to rebalance a portfolio.

Reblance the portfolio every n number of days, which is given as `shift_size`. When rebalancing, you should look back a certain number of days of data in the past, denoted as `chunk_size`. Using this data, compute the optoimal weights using `get_optimal_weights` and `get_covariance_returns`.

In [46]:
def rebalance_portfolio(returns, index_weights, shift_size, chunk_size):
    """
    Get weights for each rebalancing of the portfolio.

    Parameters
    ----------
    returns : DataFrame
        Returns for each ticker and date
    index_weights : DataFrame
        Index weight for each ticker and date
    shift_size : int
        The number of days between each rebalance
    chunk_size : int
        The number of days to look in the past for rebalancing

    Returns
    -------
    all_rebalance_weights  : list of Ndarrays
        The ETF weights for each point they are rebalanced
    """
    assert returns.index.equals(index_weights.index)
    assert returns.columns.equals(index_weights.columns)
    assert shift_size > 0
    assert chunk_size >= 0
    
    #TODO: Implement function
    
    #returns = returns.reset_index(drop=True)
    #index_weights = index_weights.reset_index(drop=True)
    
    weights_matrices = []
    for i in range(0, len(returns), shift_size):
        if i + chunk_size <= len(returns):
            chunk_returns = returns.iloc[i:i+chunk_size]
        else:
            break

        covariance_returns = get_covariance_returns(chunk_returns)
        
        if i + chunk_size <= len(returns):
            index_position = i + chunk_size - 1
            if index_position < len(index_weights):
                index_weights_chunk = index_weights.iloc[index_position]
            else:
                break
        else:
            break

        weights = get_optimal_weights(covariance_returns, index_weights_chunk, scale=2.0)

        weights_matrices.append(weights)
    
    return weights_matrices

project_tests.test_rebalance_portfolio(rebalance_portfolio)

Tests Passed


Run the following cell to rebalance the portfolio using `rebalance_portfolio`.

In [45]:
chunk_size = 250
shift_size = 5
all_rebalance_weights = rebalance_portfolio(returns, index_weights, shift_size, chunk_size)

ticker             AAL        AAPL        ABBV         ABT         AGN  \
date                                                                     
2013-07-01         nan         nan         nan         nan         nan   
2013-07-02 -0.02202381  0.02265285  0.01441961 -0.00485298 -0.01283482   
2013-07-03  0.01947657  0.00551985  0.00047382 -0.01749857  0.00129209   
2013-07-05  0.00537313 -0.00803232  0.01160313  0.01956204  0.01919510   
2013-07-08  0.00593824 -0.00567773  0.02247191  0.01403207  0.00094959   
2013-07-09  0.02479339  0.01758824 -0.00824176 -0.01892121 -0.00616650   
2013-07-10 -0.01094470 -0.00383568  0.01361958  0.00000000 -0.01304590   
2013-07-11  0.01164822  0.01558719  0.00614894  0.02216465  0.00749577   
2013-07-12  0.01093840 -0.00182079  0.02900868 -0.00141363  0.00944000   
2013-07-15  0.01138952  0.00218049 -0.00954495  0.00453001 -0.00792519   
2013-07-16  0.01069820  0.00644535 -0.01815329  0.00620068 -0.01869308   
2013-07-17  0.02785515  0.00026732  0.

ticker             AAL        AAPL        ABBV         ABT         AGN  \
date                                                                     
2013-07-09  0.02479339  0.01758824 -0.00824176 -0.01892121 -0.00616650   
2013-07-10 -0.01094470 -0.00383568  0.01361958  0.00000000 -0.01304590   
2013-07-11  0.01164822  0.01558719  0.00614894  0.02216465  0.00749577   
2013-07-12  0.01093840 -0.00182079  0.02900868 -0.00141363  0.00944000   
2013-07-15  0.01138952  0.00218049 -0.00954495  0.00453001 -0.00792519   
2013-07-16  0.01069820  0.00644535 -0.01815329  0.00620068 -0.01869308   
2013-07-17  0.02785515  0.00026732  0.00342388  0.00336134 -0.00618691   
2013-07-18 -0.00162602  0.00336502  0.00818926 -0.00335008  0.01859436   
2013-07-19 -0.01031488 -0.01576809  0.00451264  0.00476190  0.00860474   
2013-07-22 -0.00438837  0.00320038  0.01010782 -0.00195149  0.02001276   
2013-07-23 -0.00550964 -0.01717060 -0.01467645  0.02458101 -0.01188150   
2013-07-24  0.02493075  0.05136161 -0.

ticker             AAL        AAPL        ABBV         ABT         AGN  \
date                                                                     
2013-07-16  0.01069820  0.00644535 -0.01815329  0.00620068 -0.01869308   
2013-07-17  0.02785515  0.00026732  0.00342388  0.00336134 -0.00618691   
2013-07-18 -0.00162602  0.00336502  0.00818926 -0.00335008  0.01859436   
2013-07-19 -0.01031488 -0.01576809  0.00451264  0.00476190  0.00860474   
2013-07-22 -0.00438837  0.00320038  0.01010782 -0.00195149  0.02001276   
2013-07-23 -0.00550964 -0.01717060 -0.01467645  0.02458101 -0.01188150   
2013-07-24  0.02493075  0.05136161 -0.01512074 -0.00627045  0.00268966   
2013-07-25  0.01783784 -0.00456289  0.01374885  0.00356653  0.01656805   
2013-07-26  0.01380775  0.00567845  0.01243219  0.00546747  0.02995731   
2013-07-29  0.00733368  0.01541985  0.00602813 -0.00108755  0.01333735   
2013-07-30 -0.00156006  0.01234954 -0.00798935  0.00381056  0.00669244   
2013-07-31  0.00781250 -0.00174270  0.

ticker             AAL        AAPL        ABBV         ABT         AGN  \
date                                                                     
2013-07-23 -0.00550964 -0.01717060 -0.01467645  0.02458101 -0.01188150   
2013-07-24  0.02493075  0.05136161 -0.01512074 -0.00627045  0.00268966   
2013-07-25  0.01783784 -0.00456289  0.01374885  0.00356653  0.01656805   
2013-07-26  0.01380775  0.00567845  0.01243219  0.00546747  0.02995731   
2013-07-29  0.00733368  0.01541985  0.00602813 -0.00108755  0.01333735   
2013-07-30 -0.00156006  0.01234954 -0.00798935  0.00381056  0.00669244   
2013-07-31  0.00781250 -0.00174270  0.01744966 -0.00677874 -0.00819914   
2013-08-01  0.00155039  0.00916182 -0.00505717  0.00573301  0.01124600   
2013-08-02 -0.02373581  0.01284061  0.00154696 -0.00244300  0.00081013   
2013-08-05  0.01321353  0.01493925 -0.01345984 -0.00816327  0.00706454   
2013-08-06 -0.01304121 -0.00894664  0.00380228 -0.00960219 -0.00898794   
2013-08-07 -0.00264271 -0.00058033 -0.

ticker             AAL        AAPL        ABBV         ABT         AGN  \
date                                                                     
2013-07-30 -0.00156006  0.01234954 -0.00798935  0.00381056  0.00669244   
2013-07-31  0.00781250 -0.00174270  0.01744966 -0.00677874 -0.00819914   
2013-08-01  0.00155039  0.00916182 -0.00505717  0.00573301  0.01124600   
2013-08-02 -0.02373581  0.01284061  0.00154696 -0.00244300  0.00081013   
2013-08-05  0.01321353  0.01493925 -0.01345984 -0.00816327  0.00706454   
2013-08-06 -0.01304121 -0.00894664  0.00380228 -0.00960219 -0.00898794   
2013-08-07 -0.00264271 -0.00058033 -0.00690731 -0.00470914 -0.00140097   
2013-08-08  0.00582936 -0.00197858  0.01099394 -0.00027832 -0.00745773   
2013-08-09 -0.02002107 -0.01422963 -0.00776742 -0.00083519 -0.00409165   
2013-08-12  0.01182796  0.02840797  0.00738090  0.00027863 -0.00470606   
2013-08-13 -0.13071201  0.04752225 -0.00244227  0.00111421  0.01050736   
2013-08-14 -0.01161369  0.01824050 -0.

...

ticker             AAL        AAPL        ABBV         ABT         AGN  \
date                                                                     
2016-06-01  0.00125353 -0.01401963 -0.00158907 -0.00328034  0.02820785   
2016-06-02 -0.00876369 -0.00751574  0.03597008  0.00075949  0.01947195   
2016-06-03 -0.02715504  0.00204666 -0.00138270 -0.00885403 -0.00064746   
2016-06-06  0.01460565  0.00725082 -0.03353846 -0.00025523  0.00101231   
2016-06-07  0.03518874  0.00405556  0.00445718 -0.00612714  0.00934428   
2016-06-08  0.00463535 -0.00090882 -0.02171157 -0.00051374  0.00172331   
2016-06-09  0.02737619  0.00717607 -0.01587559 -0.00102801 -0.01020204   
2016-06-10 -0.00778443 -0.00822880  0.00411523 -0.01209159 -0.02615198   
2016-06-13 -0.04043452 -0.01507639 -0.01754098 -0.01406250  0.01087453   
2016-06-14 -0.04528302  0.00123279 -0.00050058 -0.00528262  0.00225826   
2016-06-15  0.00428195 -0.00328340  0.00834725 -0.00610728 -0.02031954   
2016-06-16 -0.04427681  0.00422071  0.

ticker             AAL        AAPL        ABBV         ABT         AGN  \
date                                                                     
2016-06-08  0.00463535 -0.00090882 -0.02171157 -0.00051374  0.00172331   
2016-06-09  0.02737619  0.00717607 -0.01587559 -0.00102801 -0.01020204   
2016-06-10 -0.00778443 -0.00822880  0.00411523 -0.01209159 -0.02615198   
2016-06-13 -0.04043452 -0.01507639 -0.01754098 -0.01406250  0.01087453   
2016-06-14 -0.04528302  0.00123279 -0.00050058 -0.00528262  0.00225826   
2016-06-15  0.00428195 -0.00328340  0.00834725 -0.00610728 -0.02031954   
2016-06-16 -0.04427681  0.00422071  0.00827815  0.00187016 -0.00773605   
2016-06-17  0.00686342 -0.02275756 -0.01461412 -0.00293333 -0.00943993   
2016-06-20  0.01261077 -0.00241267  0.00166639  0.00962824  0.00089343   
2016-06-21  0.01043420  0.00851735 -0.00216270 -0.00052980 -0.01576979   
2016-06-22 -0.00433045 -0.00375352  0.00683561  0.02676915 -0.01295616   
2016-06-23  0.01472064  0.00575615  0.

ticker             AAL        AAPL        ABBV         ABT         AGN  \
date                                                                     
2016-06-15  0.00428195 -0.00328340  0.00834725 -0.00610728 -0.02031954   
2016-06-16 -0.04427681  0.00422071  0.00827815  0.00187016 -0.00773605   
2016-06-17  0.00686342 -0.02275756 -0.01461412 -0.00293333 -0.00943993   
2016-06-20  0.01261077 -0.00241267  0.00166639  0.00962824  0.00089343   
2016-06-21  0.01043420  0.00851735 -0.00216270 -0.00052980 -0.01576979   
2016-06-22 -0.00433045 -0.00375352  0.00683561  0.02676915 -0.01295616   
2016-06-23  0.01472064  0.00575615  0.01523431  0.02297367  0.02170203   
2016-06-24 -0.10814375 -0.02809573 -0.02365030 -0.04340146 -0.03336046   
2016-06-27 -0.06580407 -0.01456103 -0.01971266 -0.02532313 -0.03650540   
2016-06-28  0.05935892  0.01684050  0.02232447  0.01650880  0.04708479   
2016-06-29  0.03474038  0.00865477  0.03033839  0.02689031  0.01242754   
2016-06-30  0.02202166  0.01271186  0.

ticker             AAL        AAPL        ABBV         ABT         AGN  \
date                                                                     
2016-06-22 -0.00433045 -0.00375352  0.00683561  0.02676915 -0.01295616   
2016-06-23  0.01472064  0.00575615  0.01523431  0.02297367  0.02170203   
2016-06-24 -0.10814375 -0.02809573 -0.02365030 -0.04340146 -0.03336046   
2016-06-27 -0.06580407 -0.01456103 -0.01971266 -0.02532313 -0.03650540   
2016-06-28  0.05935892  0.01684050  0.02232447  0.01650880  0.04708479   
2016-06-29  0.03474038  0.00865477  0.03033839  0.02689031  0.01242754   
2016-06-30  0.02202166  0.01271186  0.00161786  0.01918590  0.00234223   
2016-07-01  0.03602967  0.00303347  0.01292198  0.00585093  0.01267904   
2016-07-05 -0.01363791 -0.00938575 -0.01259767 -0.00252908  0.00846082   
2016-07-06 -0.02004839  0.00568481  0.02341731  0.03524341  0.00415254   
2016-07-07  0.03703704  0.00429185  0.00094682  0.01298065  0.00434636   
2016-07-08  0.02176871  0.00771315  0.

ticker             AAL        AAPL        ABBV         ABT         AGN  \
date                                                                     
2016-06-29  0.03474038  0.00865477  0.03033839  0.02689031  0.01242754   
2016-06-30  0.02202166  0.01271186  0.00161786  0.01918590  0.00234223   
2016-07-01  0.03602967  0.00303347  0.01292198  0.00585093  0.01267904   
2016-07-05 -0.01363791 -0.00938575 -0.01259767 -0.00252908  0.00846082   
2016-07-06 -0.02004839  0.00568481  0.02341731  0.03524341  0.00415254   
2016-07-07  0.03703704  0.00429185  0.00094682  0.01298065  0.00434636   
2016-07-08  0.02176871  0.00771315  0.01150875  0.01281431  0.01083988   
2016-07-11  0.03728362  0.00310302  0.00296135  0.00549057 -0.00960140   
2016-07-12  0.11232349  0.00453702  0.01787102  0.00830959  0.00595938   
2016-07-13 -0.00605886 -0.00564566 -0.00244275 -0.00565105  0.00613267   
2016-07-14  0.04150943  0.01982038 -0.01775513  0.00738623  0.01260522   
2016-07-15  0.00027871 -0.00010122 -0.

## Portfolio Turnover
With the portfolio rebalanced, we need to use a metric to measure the cost of rebalancing the portfolio. Implement `get_portfolio_turnover` to calculate the annual portfolio turnover. We'll be using the formulas used in the classroom:

$ AnnualizedTurnover =\frac{SumTotalTurnover}{NumberOfRebalanceEvents} * NumberofRebalanceEventsPerYear $

$ SumTotalTurnover =\sum_{t,n}{\left | x_{t,n} - x_{t+1,n} \right |} $ Where $ x_{t,n} $ are the weights at time $ t $ for equity $ n $.

$ SumTotalTurnover $ is just a different way of writing $ \sum \left | x_{t_1,n} - x_{t_2,n} \right | $

In [51]:
def get_portfolio_turnover(all_rebalance_weights, shift_size, rebalance_count, n_trading_days_in_year=252):
    """
    Calculage portfolio turnover.

    Parameters
    ----------
    all_rebalance_weights : list of Ndarrays
        The ETF weights for each point they are rebalanced
    shift_size : int
        The number of days between each rebalance
    rebalance_count : int
        Number of times the portfolio was rebalanced
    n_trading_days_in_year: int
        Number of trading days in a year

    Returns
    -------
    portfolio_turnover  : float
        The portfolio turnover
    """
    assert shift_size > 0
    assert rebalance_count > 0
    
    #TODO: Implement function
    
    sum_total_turnover = 0
    
    for i in range(1,len(all_rebalance_weights)):
        sum_total_turnover += sum(np.abs(all_rebalance_weights[i-1] - all_rebalance_weights[i]))
    number_rebalance_events_year = n_trading_days_in_year//shift_size
    
    portfolio_turnover = (sum_total_turnover/rebalance_count) * number_rebalance_events_year
    
    return portfolio_turnover 

project_tests.test_get_portfolio_turnover(get_portfolio_turnover)

SyntaxError: invalid syntax (<ipython-input-51-43ada661f277>, line 32)

Run the following cell to get the portfolio turnover from  `get_portfolio turnover`.

In [ ]:
print(get_portfolio_turnover(all_rebalance_weights, shift_size, len(all_rebalance_weights) - 1))

That's it! You've built a smart beta portfolio in part 1 and did portfolio optimization in part 2. You can now submit your project.

## Submission
Now that you're done with the project, it's time to submit it. Click the submit button in the bottom right. One of our reviewers will give you feedback on your project with a pass or not passed grade. You can continue to the next section while you wait for feedback.